In [17]:
import os

import torch as th
from torch import nn
import gymnasium as gym
import panda_gym
from sb3_contrib import TQC
from huggingface_sb3 import load_from_hub, package_to_hub
import optuna
from stable_baselines3 import A2C, PPO
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.vec_env import DummyVecEnv, VecNormalize
from stable_baselines3.common.env_util import make_vec_env
from stable_baselines3.common.torch_layers import BaseFeaturesExtractor, FlattenExtractor
from huggingface_hub import notebook_login

In [3]:
env_id = "PandaPickAndPlace-v3"

In [22]:
env = make_vec_env(env_id, n_envs=16)
env = VecNormalize(env,norm_obs=True, norm_reward=True, clip_obs=20.)

argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886
argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color

In [28]:
policy_tqc = dict(net_arch=dict(pi=[1024, 1024, 1024],qf=[1024, 1024, 1024]), n_critics=4, n_quantiles=25)

In [29]:
model = TQC(
    "MultiInputPolicy",
    env,
    policy_kwargs=policy_tqc,
    verbose=1,
    learning_rate=1e-3,
    ent_coef='auto',
    buffer_size=1_000_000,
    learning_starts=5_000,
    batch_size=2048,
    tau=0.005,
    gamma=0.95,
    train_freq=1,
    gradient_steps=1,
    target_entropy="auto",
    action_noise=None,
    tensorboard_log="./TQC" + env_id + "/",
)

Using cuda device


In [30]:
model.learn(1_000_000)

Logging to ./tqcPandaPickAndPlace-v3/TQC_3
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 43.9     |
|    ep_rew_mean     | -43.8    |
|    success_rate    | 0.125    |
| time/              |          |
|    episodes        | 4        |
|    fps             | 924      |
|    time_elapsed    | 0        |
|    total_timesteps | 800      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 43.9     |
|    ep_rew_mean     | -43.8    |
|    success_rate    | 0.125    |
| time/              |          |
|    episodes        | 8        |
|    fps             | 922      |
|    time_elapsed    | 0        |
|    total_timesteps | 800      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 43.9     |
|    ep_rew_mean     | -43.8    |
|    success_rate    | 0.125    |
| time/              |          |
|    

In [31]:
model.save("tqc-PandaPickAndPlace-v3-ver2")
env.save("PandaPickAndPlace_vec_normalize_tqc_ver2.pkl")

In [32]:
eval_env = DummyVecEnv([lambda: gym.make("PandaPickAndPlace-v3")])
eval_env = VecNormalize.load("PandaPickAndPlace_vec_normalize_tqc_ver2.pkl", eval_env)

# We need to override the render_mode
eval_env.render_mode = "rgb_array"

#  do not update them at test time
eval_env.training = False
# reward normalization is not needed at test time
eval_env.norm_reward = False

# Load the agent
model = TQC.load("tqc-PandaPickAndPlace-v3-ver2")

mean_reward, std_reward = evaluate_policy(model, eval_env)

print(f"Mean reward = {mean_reward:.2f} +/- {std_reward:.2f}")

argv[0]=--background_color_red=0.8745098114013672
argv[1]=--background_color_green=0.21176470816135406
argv[2]=--background_color_blue=0.1764705926179886


/home/tomek/pytorch_learning/venv/lib/python3.10/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Mean reward = -24.80 +/- 20.92


In [33]:
notebook_login()
!git config --global credential.helper store

In [34]:
from huggingface_sb3 import package_to_hub

package_to_hub(
    model=model,
    model_name=f"tqc-{env_id}",
    model_architecture="TQC",
    env_id=env_id,
    eval_env=eval_env,
    repo_id=f"Hevagog/tqc-{env_id}",
    commit_message="Improved TQC model for PandaPickAndPlace-v3",
)

ℹ This function will save, evaluate, generate a video of your agent,
create a model card and push everything to the hub. It might take up to 1min.
This is a work in progress: if you encounter a bug, please open an issue.


/home/tomek/pytorch_learning/venv/lib/python3.10/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Saving video to /tmp/tmp65hd55y4/-step-0-to-step-1000.mp4
Moviepy - Building video /tmp/tmp65hd55y4/-step-0-to-step-1000.mp4.
Moviepy - Writing video /tmp/tmp65hd55y4/-step-0-to-step-1000.mp4



ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab

Moviepy - Done !
Moviepy - video ready /tmp/tmp65hd55y4/-step-0-to-step-1000.mp4


...

policy.pth:   0%|          | 0.00/77.5M [00:00<?, ?B/s]

tqc-PandaPickAndPlace-v3.zip:   0%|          | 0.00/164M [00:00<?, ?B/s]

vec_normalize.pkl:   0%|          | 0.00/3.32k [00:00<?, ?B/s]

ℹ Your model is pushed to the Hub. You can view your model here:
https://huggingface.co/Hevagog/tqc-PandaPickAndPlace-v3/tree/main/


CommitInfo(commit_url='https://huggingface.co/Hevagog/tqc-PandaPickAndPlace-v3/commit/ae9e9cb0e1080cc230838144b1dea8d5fd816142', commit_message='Improved TQC model for PandaPickAndPlace-v3', commit_description='', oid='ae9e9cb0e1080cc230838144b1dea8d5fd816142', pr_url=None, pr_revision=None, pr_num=None)

In [23]:
class LSTMExtractor(BaseFeaturesExtractor):
    def __init__(self, observation_space, features_dim=256):
        super(LSTMExtractor, self).__init__(observation_space, features_dim)
        n_input = observation_space.shape[0]
        self.features_extractor = nn.LSTM(n_input, features_dim, batch_first=True)

    def forward(self, observations: th.Tensor) -> th.Tensor:
        # Extract features
        features, _ = self.features_extractor(observations)
        return features

In [24]:
extractor = LSTMExtractor(env.observation_space)


TypeError: 'NoneType' object is not subscriptable

In [14]:
def objective(trial: optuna.Trial):

    learning_rate = trial.suggest_float("learning_rate", 1e-5, 1e-3, log=True)
    ent_coef = trial.suggest_float("ent_coef", 0.0, 0.1)
    tau = trial.suggest_float("tau", 0.001, 0.1)
    gamma = trial.suggest_float("gamma", 0.9, 0.99)
    batch_size = trial.suggest_int("batch_size", 512, 2048)
    train_freq = trial.suggest_int("train_freq", 1, 10)
    buffer_size = trial.suggest_categorical("buffer_size", (1_000_000, 1_250_000, 1_500_000))
    gradient_steps = trial.suggest_categorical("gradient_steps", (1, 5, 10))

    model = TQC(
        "MultiInputPolicy",
        env,
        policy_kwargs=policy_tqc,
        verbose=0,
        learning_rate=learning_rate,
        ent_coef=ent_coef,
        buffer_size=buffer_size,
        learning_starts=5_000,
        batch_size=batch_size,
        tau=tau,
        gamma=gamma,
        train_freq=train_freq,
        gradient_steps=gradient_steps,
        target_entropy="auto",
        action_noise=None,
        tensorboard_log="./tqc" + env_id + "/",
    )

    model.learn(total_timesteps=int(1e5), tb_log_name=f"tqc_{trial.number}")
    mean_reward, _ = evaluate_policy(model, env, n_eval_episodes=10)
    return mean_reward

In [15]:
study = optuna.create_study(direction="maximize", study_name="tqc")

[I 2024-06-06 23:11:39,011] A new study created in memory with name: tqc


In [16]:
study.optimize(objective, n_trials=4, timeout=600)

[I 2024-06-06 23:14:25,957] Trial 0 finished with value: -50.0 and parameters: {'num_layers': 4, 'n_critics': 3, 'learning_rate': 0.0004688535532447768, 'ent_coef': 0.0036826461415357284, 'tau': 0.017315209648200033, 'gamma': 0.9773742560335635, 'batch_size': 1055, 'train_freq': 7, 'buffer_size': 1500000, 'gradient_steps': 1}. Best is trial 0 with value: -50.0.
[W 2024-06-06 23:15:34,610] Trial 1 failed with parameters: {'num_layers': 4, 'n_critics': 4, 'learning_rate': 3.143092141142597e-05, 'ent_coef': 0.06231862437468016, 'tau': 0.07172173482003612, 'gamma': 0.9699754382338025, 'batch_size': 1187, 'train_freq': 4, 'buffer_size': 1000000, 'gradient_steps': 1} because of the following error: KeyboardInterrupt().
Traceback (most recent call last):
  File "/home/tomek/pytorch_learning/venv/lib/python3.10/site-packages/optuna/study/_optimize.py", line 196, in _run_trial
    value_or_values = func(trial)
  File "/tmp/ipykernel_13201/42892611.py", line 36, in objective
    model.learn(tota

KeyboardInterrupt: 